**Tabla de contenido**
- [Introducción](#Introduccion)
- [Librerías](#Lib)
- [Análisis exploratorio](#EDA)
- [Preprocesamiento](#Preprocesamiento)
- [Modelado](#Modelado)
    - [Feature importance](#Feature-importance)

# Introduccion

En este cuaderno analizaremos un conjunto de datos sobre cáncer de mama que contiene 100 registros y 3,001 características. El objetivo es entrenar un modelo de clasificación binaria para predecir la probabilidad de cáncer de mama (clases positivo/negativo)

# Lib

In [17]:
import pandas as pd
import numpy as np
import os

# Gráficar
import plotly.subplots as sp
import plotly.graph_objects as go
import plotly.colors as pc
import plotly.express as px
import matplotlib.pyplot as plt

# Machine Learning
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import loguniform
from sklearn.linear_model import LogisticRegressionCV, LogisticRegression
from sklearn.metrics import accuracy_score


In [2]:
# lectura de datos
path_data = os.path.join(os.getcwd(), 'data')
path_file = lambda file: os.path.join(path_data, file)

df = pd.read_csv(path_file('Cancer de mama.csv'))
df.shape

(100, 3002)

Podemos observar que el DataFrame contiene **100 registros** y **3002 características**. Esto representa un caso de **alta dimensionalidad** con pocos datos, donde el número de características es considerablemente mayor que el número de observaciones, es decir,$$p>>n$$

In [3]:
df.head()

Unnamed: 0  Outcome          oov          ehx          dln          vis  \
0           1    False  2086.344056  4048.272128  3469.194600  1933.241869   
1           2     True  2086.422670  4244.170173  3470.674324  1933.691786   
2           3     True  2087.097290  4108.133526  3461.172501  1936.288530   
3           4    False  2086.705329  4159.550050  3469.221284  1932.307051   
4           5    False  2087.146315  4184.105960  3459.076523  1937.535031   

           toe         sld          kvn          bcu  ...         vqj  \
0  3883.949034  397.453079  4662.651916  4571.943113  ...  457.254147   
1  3777.372308  343.210658  4661.013687  4574.866585  ...  461.813715   
2  3880.453465  382.292746  4662.733091  4571.962473  ...  451.228498   
3  3788.490339  355.783690  4660.854216  4565.683385  ...  506.457989   
4  3870.993677  350.820529  4661.016110  4568.012707  ...  383.162593   

           jhl          uut          wpn          sig          kdf  \
0  1659.619318  2862.136537  3135.190032   350.788035  1558.948848   
1  1656.414376  2057.955525  3136.107271   976.165028  4230.445720   
2  1653.626224  2970.955995  3136.858378  1001.333294  4012.426153   
3  1657.836619  3535.031196  3136.258201  1134.623963  4271.720386   
4  1660.875245  3644.888471  3136.808653   392.442861  2475.783137   

           jsy          ghk          yil          utu  
0  4472.847124  2675.685514  2857.704611   804.414247  
1  4471.069508  2560.653847  2857.446750   373.143841  
2  4469.252496  2677.071907  2870.133280  2670.550044  
3  4472.332737  2660.481216  2856.174872  1461.926366  
4  4471.046925  2614.229494  2868.795588  1777.424582  

[5 rows x 3002 columns]

# EDA

En vista de que hay muchas caracteristicas, no enfocaremos en revisar:
- Balance de las clases
- Identificar valores faltantes
- Box plot de las caracteríticas independientes.

In [4]:
target = df['Outcome'].map({True: 1, False: 0})
features = df.drop(columns=['Outcome','Unnamed: 0'], axis=1)
print(target.value_counts()) # Valnce de la variable objetivo

Outcome
0    50
1    50
Name: count, dtype: int64


Podemos observar que las clases están balanceadas. Ahora veamos la distribución estadística de estas clase.

In [5]:
print("Valores faltantes por columna:", features.isnull().sum().sum())

Valores faltantes por columna: 0


In [6]:
def plot_boxplots(df, title='Boxplots por variable', height=300):
    """
    Genera un boxplot interactivo con colores variados para cada columna numérica del DataFrame.

    Parámetros:
    - df: pandas.DataFrame con los datos
    - title: título del gráfico
    - height: altura del gráfico en píxeles
    """
    fig = go.Figure()

    numeric_cols = df.select_dtypes(include='number').columns
    colors = pc.qualitative.Plotly  # paleta de colores categóricos

    for i, column in enumerate(numeric_cols):
        fig.add_trace(go.Box(
            y=df[column],
            name=column,
            boxpoints='outliers',
            marker=dict(size=4, color=colors[i % len(colors)]),
            line=dict(color=colors[i % len(colors)]),
            fillcolor=colors[i % len(colors)],
        ))

    fig.update_layout(
        title=title,
        yaxis_title='Valor',
        boxmode='group',
        template='plotly_white',
        font=dict(family='Arial', size=14),
        margin=dict(l=40, r=40, t=60, b=40),
        height=height,
        showlegend=False,
    )

    fig.show()
plot_boxplots(features, title='Distribución de variables numéricas', height=300)

Las características presentan difetentes rangos, lo que indica la necesita de hacer un RobustScaler. Veamos las correlaciones entre las características y la variable objetivo.

In [7]:
correlation = df.corr().dropna()['Outcome'].sort_values(ascending=False)
correlation.head(10)

Outcome    1.000000
myi        0.302649
sbx        0.287157
xqt        0.282283
pvt        0.282056
vgk        0.279947
wxa        0.276741
vll        0.275905
bpc        0.274524
jla        0.273884
Name: Outcome, dtype: float64

El valor más alto de correlación postivo se obtiene con la variable myi, que equivale a 0.3

# Preprocesamiento

En vista de que las vaiables predictoras tienen diferentes escalas, vamos a escalar los datos. En este caso usararemos RobustScaler.
El RobustScaler de scikit-learn escala los datos usando la **mediana** y el **rango intercuartílico** (IQR), lo que lo hace robusto frente a outliers.

El `RobustScaler` transforma cada valor \( x \) usando la siguiente fórmula:

$$
x_{\text{scaled}} = \frac{x - \text{mediana}(X)}{\text{IQR}(X)}
$$

donde:
- $\text{mediana}(X) = \text{Percentil}_{50}(X)$
- $\text{IQR}(X) = Q_3 - Q_1$

donde:
- $Q_1$ es el percentil 25
- $Q_3$ es el percentil 75



In [8]:
def escalar_datos(df):
    scaler = preprocessing.RobustScaler()
    df_scaled = pd.DataFrame(scaler.fit_transform(df), 
                             columns=df.columns,
                             index=df.index)
    return df_scaled
features_scaled = escalar_datos(features)

In [19]:
plot_boxplots(features_scaled, title='Distribución de variables numéricas', height=300)

# Modelado

Antes de entrenar el modelo, vamos a dividir los datos en entrenamiento y test.

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    features_scaled, target, test_size=0.2, random_state=42, shuffle=True
)

model = LogisticRegressionCV(
    Cs=50,                    # Equivalente a distintos valores de λ
    cv=5,                     # Validación cruzada 5-fold
    penalty='l1',             # Lasso (como en Modelo C)
    solver='liblinear',       # Requerido para L1
    scoring='neg_mean_squared_error',  
    refit=True
)

model.fit(features_scaled, target)

LogisticRegressionCV(Cs=50, cv=5, penalty='l1',
                     scoring='neg_mean_squared_error', solver='liblinear')

In [10]:
# Predecir en el conjunto de prueba
y_pred = model.predict(X_test)

# Calcular el accuracy
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy en el conjunto de prueba: {accuracy:.4f}")

Accuracy en el conjunto de prueba: 1.0000


## Feature importance

In [38]:
# Veamos las caracteristicas importantes
coeficientes = model.coef_
coeficientes = coeficientes.reshape(-1)
nombres_caracteristicas = [f'Feature_{i}' for i in range(features_scaled.shape[1])]

df_coeficientes = pd.DataFrame({
    'Caracteristica': nombres_caracteristicas,
    'Coeficiente': coeficientes,
    'Importancia_abs': abs(coeficientes)
})
# Ordenar por importancia absoluta (los más lejos de cero son más importantes)
df_coeficientes = df_coeficientes.sort_values('Importancia_abs', ascending=False)
caracteristicas_seleccionadas = df_coeficientes[df_coeficientes['Coeficiente'] != 0]
caracteristicas_seleccionadas = caracteristicas_seleccionadas.sort_values('Importancia_abs', ascending=True)



In [39]:

def plotbar(df, y, x, colors, labels, text_fmt, title):
    fig = px.bar(
        df,
        y=y,
        x=x,
        orientation='h',
        labels=labels,
        title=title,
        color_discrete_sequence=colors,
        color=y,
        text_auto='.2f',
        height=600,
    )

    fig.update_traces(texttemplate=text_fmt)

    fig.update_layout(
        title=dict(
            x=0.5,
            font=dict(size=18, family='Arial', color='black')
        ),
        plot_bgcolor='white',
        paper_bgcolor='white',
        showlegend=False,
        bargap=0.2,
        xaxis=dict(
            title_font=dict(size=14, family='Arial', color='black'),
            tickfont=dict(size=12, family='Arial', color='black'),
            showgrid=True,
            gridcolor='lightgrey',
            zerolinecolor='lightgrey'
        ),
        yaxis=dict(
            title='',
            tickfont=dict(size=12, family='Arial', color='black'),
            autorange='reversed',
            ticklen=10,
            showline=True,
            linecolor='black',
            automargin=True,
            ticksuffix="   "
        ),
        hoverlabel=dict(
            bgcolor='white',
            font_size=12,
            font_family='Arial'
        )
    )
    
    return fig


pie_colors = pc.qualitative.Plotly
bar_fig = plotbar(df=caracteristicas_seleccionadas,
                  colors=pie_colors,
                  y='Caracteristica',
                  x='Importancia_abs',
            labels={'Importancia_abs': 'Importancia_abs'},
            text_fmt ='<b>%{x:.2f}%</b>', # muestra 2 decimales y el simbolo %
            title=''

            )
bar_fig.show()